In [0]:
%%capture
%pip install --upgrade databricks-langchain langchain-community langchain langchainhub langgraph langchain_databricks databricks-sql-connector tiktoken streamlit faiss-cpu
%pip install duckduckgo-search 
%pip install pyvis
%pip install leidenalg python-igraph

In [0]:
dbutils.library.restartPython()

In [0]:
import warnings
warnings.filterwarnings('ignore', category=DeprecationWarning)

# 1. Random select 200 papers for test

##1.1. Read in data

In [0]:
import pandas as pd
import numpy as np
import re
from typing import List

# Read in data
jds_metadata = pd.read_csv('file:/Workspace/Users/el839@cornell.edu/1_DairyLLM/Data/jds_metadata.csv')
animal_metadata = pd.read_csv('file:/Workspace/Users/el839@cornell.edu/1_DairyLLM/Data/animal_metadata.csv')


# Cleaning to drop rows with missing abstracts
jds_cleaned = jds_metadata.copy().dropna(subset=['Abstract'])
animal_cleaned = animal_metadata.copy().dropna(subset=['Abstract'])

def extract_abstract(text):
    match = re.search(r"Author information:.*?\n\n(.*?)\n\n(?:Copyright|DOI|PMID)", text, re.DOTALL)
    if match:
        abstract = match.group(1).strip()
        abstract = re.sub(r'\s+', ' ', abstract)
        return abstract
    return None

jds_cleaned['Pure Abstract'] = jds_cleaned['Abstract'].apply(extract_abstract)
animal_cleaned['Pure Abstract'] = animal_cleaned['Abstract'].apply(extract_abstract)


# Combine JDS and Animal
journal_df = pd.concat([jds_cleaned,animal_cleaned])[['Title','Pure Abstract','Authors','Publication Date','DOI','Link','Affiliations','PubMed ID','Publication Year','Country']]

journal_df_cleaned = journal_df.dropna(subset=['Pure Abstract'], how='any')

print(journal_df_cleaned.shape)


/root/.ipykernel/4157/command-5206377055545860-3605538287:7: DtypeWarning: Columns (2,7,8,21) have mixed types. Specify dtype option on import or set low_memory=False.
  jds_metadata = pd.read_csv('file:/Workspace/Users/el839@cornell.edu/1_DairyLLM/Data/jds_metadata.csv')


(23085, 10)


In [0]:
jds_test= journal_df_cleaned.sample(n=200)[['Title','Pure Abstract','Publication Date','DOI','Affiliations','PubMed ID','Country']]
print(jds_test.shape)
display(jds_test.head())

(200, 7)


Title Pure Abstract Publication Date DOI Affiliations PubMed ID Country Feed substrates influence biofilm formation on reverse osmosis membranes and their cleaning efficiency The dairy industry is increasingly using reverse osmosis (RO) membranes for concentration of various fluid feed materials such as whey and ultrafiltration (UF) permeate. This study compared the effect of UF permeate and whey on membrane biofilm formation. A Bacillus sp., previously isolated in our laboratory from a cleaning-resistant membrane biofilm, was used to develop 48-h-old static biofilms on RO membrane pieces, using the different feed substrates (UF permeate, whey, and an alternating whey/UF feed). Biofilms were analyzed for viable counts by the swab technique, and we used scanning electron and atomic force microscopy for microstructure imaging. The membrane cleaning process included 6 sequential steps. We observed differences in the resistance pattern of the 3 types of biofilms to the typical cleaning process. The mean pretreatment counts of the 48-h UF permeate biofilms were 5.39 log cfu/cm2, much higher than the whey biofilm counts of 3.44 log, and alternating whey/UF biofilm counts of 4.54 log. After a 6-step cleaning cycle, we found 2.54 log survivors of the Bacillus isolate on UF biofilms, whereas only 1.82 log survivors were found in whey biofilm, and 2.14 log survivors on whey/UF permeate biofilms. In conclusion, the UF permeate biofilms was more resistant to the biofilm cleaning process compared with the whey or whey/UF permeate biofilms. Scanning electron micrographs showed different microstructures of biofilms based on the type of feed. For UF permeate and whey/UF permeate biofilms, bacilli were present in multilayers of cells in aggregates or irregular clusters with foulant layers. In contrast, those in whey biofilms were in monolayers, with a smoother, flatter appearance. Atomic force microscopy analysis indicated that UF permeate biofilms had the greatest surface roughness among the biofilms, reflecting intensified bacterial colonization. The biofilm micro- and nanostructure variations for the 2 feed substrates and their combination may have resulted in differences in their resistance to the cleaning process. 2018-01-01 10.3168/jds.2017-13249 South Dakota State University (Brookings, United States), Laura Chenel's Chevre (None, United States) 2.9103718E7 United States Effect of mastitis treatment and somatic cell counts on milk yield in Danish organic dairy cows Production and disease data from 17,488 lactations in 48 Danish organic dairy herds from 1997 to 2001 were analyzed to obtain estimates on the effect of somatic cell counts (SCC) and mastitis treatment on milk production. A multilevel three-parameter piecewise random coefficients linear model with energy-corrected milk (ECM) as dependent variable and herd, lactation, and test days as levels, was used to model the lactation curve. Covariates related to production, SCC, veterinary treatments, and reproductive performance in the previous lactation as well as information on other diseases in the current lactation were included to describe the production capacity of the individual cow. The average daily milk production at herd level was 20.8, 24.2, and 25.8 kg of ECM/d in first, second, and third or later lactation. The estimates for production losses were on average 0.2, 0.3, and 0.4 kg of ECM/d in first, second, and third or later lactation with each twofold increase in SCC between 100,000 and 1,500,000 cells/ml. The effect varied with the stage of lactation and was nonsignificant around 60 d postpartum and highest at the end of the lactation. The production losses in cows treated for mastitis varied with parity and stage of lactation and were modified by the SCC after treatment. For a cow in third lactation with a SCC below 100,000 cells/ ml before treatment at days in milk = 15, the predicted loss was 435 kg of ECM, including a loss of 135 kg of ECM because of higher SCC compa

##1.2. Preprocess: clean, prepare metadata, chunk, store

In [0]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.schema import Document
import pprint

# Convert the extracted text into Document objects
documents = [
    Document(
        page_content=row['Pure Abstract'], 
        metadata={col: row[col] for col in jds_test.columns if col != 'Pure Abstract'}
    )
    for _, row in jds_test.iterrows()
]

# Initialize the text splitter
splitter = RecursiveCharacterTextSplitter(
    chunk_size=600,
    chunk_overlap=100,
    length_function=len,
    is_separator_regex=False,
)

# Split the documents into chunks
chunks = splitter.split_documents(documents)

# Output the number of chunks and example chunk
print("Number of chunks = ", len(chunks))
print("------")
print("Sample chunk content:\n", chunks[3])


Number of chunks =  832
------
Sample chunk content:
 page_content='whey/UF permeate biofilms, bacilli were present in multilayers of cells in aggregates or irregular clusters with foulant layers. In contrast, those in whey biofilms were in monolayers, with a smoother, flatter appearance. Atomic force microscopy analysis indicated that UF permeate biofilms had the greatest surface roughness among the biofilms, reflecting intensified bacterial colonization. The biofilm micro- and nanostructure variations for the 2 feed substrates and their combination may have resulted in differences in their resistance to the cleaning process.' metadata={'Title': 'Feed substrates influence biofilm formation on reverse osmosis membranes and their cleaning efficiency', 'Publication Date': '2018-01-01', 'DOI': '10.3168/jds.2017-13249', 'Affiliations': "South Dakota State University (Brookings, United States), Laura Chenel's Chevre (None, United States)", 'PubMed ID': 29103718.0, 'Country': 'United States'

In [0]:
import pandas as pd
import uuid

def documents2Dataframe(documents):
    rows = []
    for chunk in documents:
        row = {
            "text": chunk.page_content,
            **chunk.metadata,
            "chunk_id": uuid.uuid4().hex,
        }
        rows = rows + [row]

    df = pd.DataFrame(rows)
    return df


df_chunks = documents2Dataframe(chunks)

print(df_chunks.shape)
# Output the DataFrame
display(df_chunks.head())  


(832, 8)


text Title Publication Date DOI Affiliations PubMed ID Country chunk_id The dairy industry is increasingly using reverse osmosis (RO) membranes for concentration of various fluid feed materials such as whey and ultrafiltration (UF) permeate. This study compared the effect of UF permeate and whey on membrane biofilm formation. A Bacillus sp., previously isolated in our laboratory from a cleaning-resistant membrane biofilm, was used to develop 48-h-old static biofilms on RO membrane pieces, using the different feed substrates (UF permeate, whey, and an alternating whey/UF feed). Biofilms were analyzed for viable counts by the swab technique, and we used scanning Feed substrates influence biofilm formation on reverse osmosis membranes and their cleaning efficiency 2018-01-01 10.3168/jds.2017-13249 South Dakota State University (Brookings, United States), Laura Chenel's Chevre (None, United States) 2.9103718E7 United States 495f35bb88864ee18467655061984b05 whey/UF feed). Biofilms were analyzed for viable counts by the swab technique, and we used scanning electron and atomic force microscopy for microstructure imaging. The membrane cleaning process included 6 sequential steps. We observed differences in the resistance pattern of the 3 types of biofilms to the typical cleaning process. The mean pretreatment counts of the 48-h UF permeate biofilms were 5.39 log cfu/cm2, much higher than the whey biofilm counts of 3.44 log, and alternating whey/UF biofilm counts of 4.54 log. After a 6-step cleaning cycle, we found 2.54 log survivors of the Bacillus Feed substrates influence biofilm formation on reverse osmosis membranes and their cleaning efficiency 2018-01-01 10.3168/jds.2017-13249 South Dakota State University (Brookings, United States), Laura Chenel's Chevre (None, United States) 2.9103718E7 United States 6e833afb1a1d4d998fc1dd903a8efb03 counts of 4.54 log. After a 6-step cleaning cycle, we found 2.54 log survivors of the Bacillus isolate on UF biofilms, whereas only 1.82 log survivors were found in whey biofilm, and 2.14 log survivors on whey/UF permeate biofilms. In conclusion, the UF permeate biofilms was more resistant to the biofilm cleaning process compared with the whey or whey/UF permeate biofilms. Scanning electron micrographs showed different microstructures of biofilms based on the type of feed. For UF permeate and whey/UF permeate biofilms, bacilli were present in multilayers of cells in aggregates or irregular Feed substrates influence biofilm formation on reverse osmosis membranes and their cleaning efficiency 2018-01-01 10.3168/jds.2017-13249 South Dakota State University (Brookings, United States), Laura Chenel's Chevre (None, United States) 2.9103718E7 United States 0f9b0bf780584e70b4357a9c0e7777cb whey/UF permeate biofilms, bacilli were present in multilayers of cells in aggregates or irregular clusters with foulant layers. In contrast, those in whey biofilms were in monolayers, with a smoother, flatter appearance. Atomic force microscopy analysis indicated that UF permeate biofilms had the greatest surface roughness among the biofilms, reflecting intensified bacterial colonization. The biofilm micro- and nanostructure variations for the 2 feed substrates and their combination may have resulted in differences in their resistance to the cleaning process. Feed substrates influence biofilm formation on reverse osmosis membranes and their cleaning efficiency 2018-01-01 10.3168/jds.2017-13249 South Dakota State University (Brookings, United States), Laura Chenel's Chevre (None, United States) 2.9103718E7 United States 69a708b04778479ea83e60c5b762caf1 Production and disease data from 17,488 lactations in 48 Danish organic dairy herds from 1997 to 2001 were analyzed to obtain estimates on the effect of somatic cell counts (SCC) and mastitis treatment on milk production. A multilevel three-parameter piecewise random coefficients linear model with energy-corrected milk (ECM) as dependent variable and herd, lactation, and t

In [0]:
# df_chunks_test= df_chunks.sample(n=100)

##1.3. Use LLM to extract concepts and edges

In [0]:
# Here is the prompt from Microsoft GraphRag. Should I try this one, or it's an overkill?
    ## Copyright (c) 2024 Microsoft Corporation. Licensed under the MIT License

GRAPH_EXTRACTION_SYSTEM = """
-Goal-
Given a text document that is potentially relevant to this activity and a list of entity types, identify all entities of those types from the text and all relationships among the identified entities.

-Steps-
1. Identify all entities. For each identified entity, extract the following information:
- entity_name: Name of the entity, capitalized
- entity_type: One of the following types: [{entity_types}]
- entity_description: Comprehensive description of the entity's attributes and activities
Format each entity as ("entity"{tuple_delimiter}<entity_name>{tuple_delimiter}<entity_type>{tuple_delimiter}<entity_description>

2. From the entities identified in step 1, identify all pairs of (source_entity, target_entity) that are *clearly related* to each other.
For each pair of related entities, extract the following information:
- source_entity: name of the source entity, as identified in step 1
- target_entity: name of the target entity, as identified in step 1
- relationship_description: explanation as to why you think the source entity and the target entity are related to each other
- relationship_strength: a numeric score indicating strength of the relationship between the source entity and target entity
 Format each relationship as ("relationship"{tuple_delimiter}<source_entity>{tuple_delimiter}<target_entity>{tuple_delimiter}<relationship_description>{tuple_delimiter}<relationship_strength>)

3. Return output in English as a single list of all the entities and relationships identified in steps 1 and 2. Use **{record_delimiter}** as the list delimiter.

4. When finished, output {completion_delimiter}

######################
-Examples-
######################
Example 1:

Entity_types: [person, technology, mission, organization, location]
Text:
while Alex clenched his jaw, the buzz of frustration dull against the backdrop of Taylor's authoritarian certainty. It was this competitive undercurrent that kept him alert, the sense that his and Jordan's shared commitment to discovery was an unspoken rebellion against Cruz's narrowing vision of control and order.

Then Taylor did something unexpected. They paused beside Jordan and, for a moment, observed the device with something akin to reverence. “If this tech can be understood..." Taylor said, their voice quieter, "It could change the game for us. For all of us.”

The underlying dismissal earlier seemed to falter, replaced by a glimpse of reluctant respect for the gravity of what lay in their hands. Jordan looked up, and for a fleeting heartbeat, their eyes locked with Taylor's, a wordless clash of wills softening into an uneasy truce.

It was a small transformation, barely perceptible, but one that Alex noted with an inward nod. They had all been brought here by different paths
################
Output:
("entity"{tuple_delimiter}"Alex"{tuple_delimiter}"person"{tuple_delimiter}"Alex is a character who experiences frustration and is observant of the dynamics among other characters."){record_delimiter}
("entity"{tuple_delimiter}"Taylor"{tuple_delimiter}"person"{tuple_delimiter}"Taylor is portrayed with authoritarian certainty and shows a moment of reverence towards a device, indicating a change in perspective."){record_delimiter}
("entity"{tuple_delimiter}"Jordan"{tuple_delimiter}"person"{tuple_delimiter}"Jordan shares a commitment to discovery and has a significant interaction with Taylor regarding a device."){record_delimiter}
("entity"{tuple_delimiter}"Cruz"{tuple_delimiter}"person"{tuple_delimiter}"Cruz is associated with a vision of control and order, influencing the dynamics among other characters."){record_delimiter}
("entity"{tuple_delimiter}"The Device"{tuple_delimiter}"technology"{tuple_delimiter}"The Device is central to the story, with potential game-changing implications, and is revered by Taylor."){record_delimiter}
("relationship"{tuple_delimiter}"Alex"{tuple_delimiter}"Taylor"{tuple_delimiter}"Alex is affected by Taylor's authoritarian certainty and observes changes in Taylor's attitude towards the device."{tuple_delimiter}7){record_delimiter}
("relationship"{tuple_delimiter}"Alex"{tuple_delimiter}"Jordan"{tuple_delimiter}"Alex and Jordan share a commitment to discovery, which contrasts with Cruz's vision."{tuple_delimiter}6){record_delimiter}
("relationship"{tuple_delimiter}"Taylor"{tuple_delimiter}"Jordan"{tuple_delimiter}"Taylor and Jordan interact directly regarding the device, leading to a moment of mutual respect and an uneasy truce."{tuple_delimiter}8){record_delimiter}
("relationship"{tuple_delimiter}"Jordan"{tuple_delimiter}"Cruz"{tuple_delimiter}"Jordan's commitment to discovery is in rebellion against Cruz's vision of control and order."{tuple_delimiter}5){record_delimiter}
("relationship"{tuple_delimiter}"Taylor"{tuple_delimiter}"The Device"{tuple_delimiter}"Taylor shows reverence towards the device, indicating its importance and potential impact."{tuple_delimiter}9){completion_delimiter}
#############################
Example 2:

Entity_types: [person, technology, mission, organization, location]
Text:
They were no longer mere operatives; they had become guardians of a threshold, keepers of a message from a realm beyond stars and stripes. This elevation in their mission could not be shackled by regulations and established protocols—it demanded a new perspective, a new resolve.

Tension threaded through the dialogue of beeps and static as communications with Washington buzzed in the background. The team stood, a portentous air enveloping them. It was clear that the decisions they made in the ensuing hours could redefine humanity's place in the cosmos or condemn them to ignorance and potential peril.

Their connection to the stars solidified, the group moved to address the crystallizing warning, shifting from passive recipients to active participants. Mercer's latter instincts gained precedence— the team's mandate had evolved, no longer solely to observe and report but to interact and prepare. A metamorphosis had begun, and Operation: Dulce hummed with the newfound frequency of their daring, a tone set not by the earthly
#############
Output:
("entity"{tuple_delimiter}"Washington"{tuple_delimiter}"location"{tuple_delimiter}"Washington is a location where communications are being received, indicating its importance in the decision-making process."){record_delimiter}
("entity"{tuple_delimiter}"Operation: Dulce"{tuple_delimiter}"mission"{tuple_delimiter}"Operation: Dulce is described as a mission that has evolved to interact and prepare, indicating a significant shift in objectives and activities."){record_delimiter}
("entity"{tuple_delimiter}"The team"{tuple_delimiter}"organization"{tuple_delimiter}"The team is portrayed as a group of individuals who have transitioned from passive observers to active participants in a mission, showing a dynamic change in their role."){record_delimiter}
("relationship"{tuple_delimiter}"The team"{tuple_delimiter}"Washington"{tuple_delimiter}"The team receives communications from Washington, which influences their decision-making process."{tuple_delimiter}7){record_delimiter}
("relationship"{tuple_delimiter}"The team"{tuple_delimiter}"Operation: Dulce"{tuple_delimiter}"The team is directly involved in Operation: Dulce, executing its evolved objectives and activities."{tuple_delimiter}9){completion_delimiter}
#############################
Example 3:

Entity_types: [person, role, technology, organization, event, location, concept]
Text:
their voice slicing through the buzz of activity. "Control may be an illusion when facing an intelligence that literally writes its own rules," they stated stoically, casting a watchful eye over the flurry of data.

"It's like it's learning to communicate," offered Sam Rivera from a nearby interface, their youthful energy boding a mix of awe and anxiety. "This gives talking to strangers' a whole new meaning."

Alex surveyed his team—each face a study in concentration, determination, and not a small measure of trepidation. "This might well be our first contact," he acknowledged, "And we need to be ready for whatever answers back."

Together, they stood on the edge of the unknown, forging humanity's response to a message from the heavens. The ensuing silence was palpable—a collective introspection about their role in this grand cosmic play, one that could rewrite human history.

The encrypted dialogue continued to unfold, its intricate patterns showing an almost uncanny anticipation
#############
Output:
("entity"{tuple_delimiter}"Sam Rivera "{tuple_delimiter}"person"{tuple_delimiter}"Sam Rivera is a member of a team working on communicating with an unknown intelligence, showing a mix of awe and anxiety."){record_delimiter}
("entity"{tuple_delimiter}"Alex"{tuple_delimiter}"person"{tuple_delimiter}"Alex is the leader of a team attempting first contact with an unknown intelligence, acknowledging the significance of their task."){record_delimiter}
("entity"{tuple_delimiter}"Control"{tuple_delimiter}"concept"{tuple_delimiter}"Control refers to the ability to manage or govern, which is challenged by an intelligence that writes its own rules."){record_delimiter}
("entity"{tuple_delimiter}"Intelligence"{tuple_delimiter}"concept"{tuple_delimiter}"Intelligence here refers to an unknown entity capable of writing its own rules and learning to communicate."){record_delimiter}
("entity"{tuple_delimiter}"First Contact"{tuple_delimiter}"event"{tuple_delimiter}"First Contact is the potential initial communication between humanity and an unknown intelligence."){record_delimiter}
("entity"{tuple_delimiter}"Humanity's Response"{tuple_delimiter}"event"{tuple_delimiter}"Humanity's Response is the collective action taken by Alex's team in response to a message from an unknown intelligence."){record_delimiter}
("relationship"{tuple_delimiter}"Sam Rivera"{tuple_delimiter}"Intelligence"{tuple_delimiter}"Sam Rivera is directly involved in the process of learning to communicate with the unknown intelligence."{tuple_delimiter}9){record_delimiter}
("relationship"{tuple_delimiter}"Alex"{tuple_delimiter}"First Contact"{tuple_delimiter}"Alex leads the team that might be making the First Contact with the unknown intelligence."{tuple_delimiter}10){record_delimiter}
("relationship"{tuple_delimiter}"Alex"{tuple_delimiter}"Humanity's Response"{tuple_delimiter}"Alex and his team are the key figures in Humanity's Response to the unknown intelligence."{tuple_delimiter}8){record_delimiter}
("relationship"{tuple_delimiter}"Control"{tuple_delimiter}"Intelligence"{tuple_delimiter}"The concept of Control is challenged by the Intelligence that writes its own rules."{tuple_delimiter}7){completion_delimiter}
#############################
"""



In [0]:
from databricks_langchain import ChatDatabricks
from langchain.prompts.chat import ChatPromptTemplate, HumanMessagePromptTemplate
import numpy as np
import pandas as pd
import json


def graphPrompt(input_text: str, metadata:{}):

    SYS_PROMPT = """
        You are a network graph maker specializing in dairy science, extracting terms and their relations from a given context. You are provided with a context chunk (delimited by ```) from the Journal of Dairy Science® (JDS). Your task is to extract the ontology of terms mentioned in the given context, focusing on key concepts in dairy science.

        Step 1: While traversing through each sentence, identify the key terms mentioned in it. Terms may include dairy-related objects, entities, processes, technologies, or concepts such as:
            - Dairy products: milk, cheese, yogurt, butter, etc.
            - Animals: dairy cows, calves, heifers, cattle breeds (e.g., Holstein, Jersey), etc.
            - Nutrition: feed, forage, silage, total mixed ration (TMR), concentrates, supplements (e.g., vitamins, minerals), etc.
            - Health: mastitis, lameness, metabolic disorders (e.g., ketosis, milk fever), vaccines, antibiotics, etc.
            - Genetics: breeding, genomics, heritability, genetic markers, selective breeding, etc.
            - Reproduction: artificial insemination, embryo transfer, estrus synchronization, fertility, etc.
            - Management: milking systems (e.g., robotic milking), herd management, housing systems, sustainability practices, etc.
            - Environment: greenhouse gas emissions, manure management, water usage, etc.
            - Processing and technology: pasteurization, homogenization, fermentation, ultrafiltration, packaging, etc.
            - Scientific domains: biochemistry, microbiology, genetics, nutrition, pathology, physiology, etc.
            - Organizations and entities: American Dairy Science Association®, government agencies, research institutions, etc.
            - Conditions and factors: milk composition (e.g., fat, protein), shelf life, spoilage, food safety, etc.
            - Terms should be as specific and atomistic as possible.

        Step 2: Identify how these terms are related to one another. Terms mentioned in the same sentence or paragraph are typically related. Relationships can include, but not limited to:
            - Process relationships: e.g., "pasteurization affects milk shelf life."
            - Compositional relationships: e.g., "milk contains lactose."
            - Causal relationships: e.g., "microbial contamination causes spoilage."
            - Functional relationships: e.g., "probiotics improve gut health."
            - Biological relationships: e.g., "genetic markers influence milk yield."
            - Management relationships: e.g., "feeding practices impact milk composition."
            - Environmental relationships: e.g., "manure management affects greenhouse gas emissions."

        Step 3: Define the relationship between each pair of related terms. Format your output ONLY as a JSON list but NOTHING ELSE:
            [
                {
                    "node_1": "A concept from extracted ontology",
                    "node_2": "A related concept from extracted ontology",
                    "edge": "Relationship between the two concepts, node_1 and node_2 in one or two sentences"
                },
                ...
            ]

    ----Example----

    Context: "Feeding cows a high-forage diet improves milk fat content, while genetic selection can enhance milk yield and disease resistance. Additionally, robotic milking systems reduce labor costs and improve milking efficiency."

    Output:
            [
        {
            "node_1": "high-forage diet",
            "node_2": "milk fat content",
            "edge": "Feeding cows a high-forage diet improves milk fat content."
        },
        {
            "node_1": "genetic selection",
            "node_2": "milk yield",
            "edge": "Genetic selection can enhance milk yield in dairy cows."
        },
        {
            "node_1": "genetic selection",
            "node_2": "disease resistance",
            "edge": "Genetic selection can improve disease resistance in dairy cows."
        },
        {
            "node_1": "robotic milking systems",
            "node_2": "labor costs",
            "edge": "Robotic milking systems reduce labor costs in dairy farming."
        },
        {
            "node_1": "robotic milking systems",
            "node_2": "milking efficiency",
            "edge": "Robotic milking systems improve milking efficiency."
        }
    ]

    Note: Focus on extracting relationships that are explicitly stated or strongly implied in the context. Avoid speculative or inferred relationships unless they are well-supported by the text.

    """

    messages = [
        {"role": "system", "content": SYS_PROMPT},
        {"role": "user", "content": f"context: ```{input_text}```"}
    ]

    llama70b = ChatDatabricks(
    endpoint="databricks-meta-llama-3-1-70b-instruct",
    temperature=0.0,
    max_tokens=1024,
    streaming=True
    )

    response = llama70b.invoke(messages)
    response_content = response.content
    
    try:
        result = json.loads(response_content)
        result = [dict(item, **metadata) for item in result]
    except json.JSONDecodeError:
        print("\n\nERROR ### Here is the buggy response: ", response_content, "\n\n")
        result = None
    
    return result


def df2Graph(dataframe: pd.DataFrame) -> list:
    # dataframe.reset_index(inplace=True)
    results = dataframe.apply(
        lambda row: graphPrompt(row.text, {"chunk_id": row.chunk_id}), axis=1
    )
    # invalid json results in NaN
    results = results.dropna()
    results = results.reset_index(drop=True)

    ## Flatten the list of lists to one single list of entities.
    concept_list = np.concatenate(results).ravel().tolist()
    return concept_list


def graph2Df(nodes_list) -> pd.DataFrame:
    ## Remove all NaN entities
    graph_dataframe = pd.DataFrame(nodes_list).replace(" ", np.nan)
    graph_dataframe = graph_dataframe.dropna(subset=["node_1", "node_2"])
    graph_dataframe["node_1"] = graph_dataframe["node_1"].apply(lambda x: x.lower())
    graph_dataframe["node_2"] = graph_dataframe["node_2"].apply(lambda x: x.lower())

    return graph_dataframe

In [0]:
regenerate = True #Set as True to regenerate the data, otherwise, just read in the csv

df_to_be_graphed = df_chunks

if regenerate:
    concepts_list = df2Graph(df_to_be_graphed)
    dfg1 = graph2Df(concepts_list)
    # dfg1.to_csv("/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/ProcessedData/graph.csv", sep="|", index=False)
    # df_chunks_test.to_csv("/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/ProcessedData/chunks.csv", sep="|", index=False)
else:
    dfg1 = pd.read_csv("/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/ProcessedData/graph.csv", sep="|")



ERROR ### Here is the buggy response:  [
    {
        "node_1": "high-concentrate diet",
        "node_2": "LW gain (LWG)",
        "edge": "High-concentrate diet leads to an improvement in LW gain (LWG) and an increase in BCS compared to a lower concentrate diet."
    },
    {
        "node_1": "high-concentrate diet",
        "node_2": "digestibility of DM",
        "edge": "High-concentrate diet increases the digestibility of DM."
    },
    {
        "node_1": "high-concentrate diet",
        "node_2": "digestibility of organic matter",
        "edge": "High-concentrate diet increases the digestibility of organic matter."
    },
    {
        "node_1": "high-concentrate diet",
        "node_2": "digestibility of CP",
        "edge": "High-concentrate diet increases the digestibility of CP."
    },
    {
        "node_1": "high-concentrate diet",
        "node_2": "digestibility of ADF",
        "edge": "High-concentrate diet increases the digestibility of ADF."
    },
    {
    

[Trace(request_id=tr-7f0cc0fa67954731838c6219b2a6f005), Trace(request_id=tr-edc3a8a612564082a0cfb512bc9a445f), Trace(request_id=tr-2d737057d12a41a0b04a280bd3dee88a), Trace(request_id=tr-e7a545319069413d8b1230057ce5580d), Trace(request_id=tr-2dfd4985eacc45ab99568eff604ab2cf), Trace(request_id=tr-5ebf408f3e9f4f1f9e0fefc95e5ed1e1), Trace(request_id=tr-f08e99a19932463f88c40d7cde3b7d92), Trace(request_id=tr-ce889ae930a743d69980aae079ef0141), Trace(request_id=tr-c5c2620f5161409fba5d484e5a1cdec3), Trace(request_id=tr-0025d0bd18de4d9aaeb1f9839bbc5644)]

In [0]:
import pandas as pd
import numpy as np

dfg1.to_csv("/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/ProcessedData/graph_test_200.csv", sep="|", index=False)

dfg1 = pd.read_csv("/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/ProcessedData/graph_test_200.csv", sep="|")
dfg1.replace("", np.nan, inplace=True)
dfg1.dropna(subset=["node_1", "node_2",'edge'], inplace=True)
dfg1.drop(columns=["node_3"], inplace=True)
dfg1['count'] = 1 ## It's just an assigned weights to count the number of times a pair of nodes are connected.  
print(dfg1.shape)
dfg1.head()

(6511, 5)


node_1  ... count
0                  dairy industry  ...     1
1  reverse osmosis (ro) membranes  ...     1
2  reverse osmosis (ro) membranes  ...     1
3   ultrafiltration (uf) permeate  ...     1
4                    bacillus sp.  ...     1

[5 rows x 5 columns]

In [0]:
# Calculating contextual proximity, which is used to measure the relationship when concepts are in the same text chunk but not directed linked together via edges. 

import numpy as np

def contextual_proximity(df: pd.DataFrame) -> pd.DataFrame:
    ## Melt the dataframe into a list of nodes
    dfg_long = pd.melt(
        df, id_vars=["chunk_id"], value_vars=["node_1", "node_2"], value_name="node"
    )
    dfg_long.drop(columns=["variable"], inplace=True)
    # Self join with chunk id as the key will create a link between terms occuring in the same text chunk.
    dfg_wide = pd.merge(dfg_long, dfg_long, on="chunk_id", suffixes=("_1", "_2"))
    # drop self loops
    self_loops_drop = dfg_wide[dfg_wide["node_1"] == dfg_wide["node_2"]].index
    dfg2 = dfg_wide.drop(index=self_loops_drop).reset_index(drop=True)
    ## Group and count edges.
    dfg2 = (
        dfg2.groupby(["node_1", "node_2"])
        .agg({"chunk_id": [",".join, "count"]})
        .reset_index()
    )
    dfg2.columns = ["node_1", "node_2", "chunk_id", "count"]
    dfg2.replace("", np.nan, inplace=True)
    dfg2.dropna(subset=["node_1", "node_2"], inplace=True)
    # Drop edges with 1 count
    dfg2 = dfg2[dfg2["count"] != 1]
    dfg2["edge"] = "Contextual proximity, indicating shared meaningful relationships."
    return dfg2

dfg2 = contextual_proximity(dfg1)
dfg2.tail()

node_1  ...                                               edge
38609  ρ-associated protein kinase 1  ...  Contextual proximity, indicating shared meanin...
38610  ρ-associated protein kinase 1  ...  Contextual proximity, indicating shared meanin...
38611  ρ-associated protein kinase 1  ...  Contextual proximity, indicating shared meanin...
38612  ρ-associated protein kinase 1  ...  Contextual proximity, indicating shared meanin...
38613  ρ-associated protein kinase 1  ...  Contextual proximity, indicating shared meanin...

[5 rows x 5 columns]

In [0]:
# Adjust weights in dfg2, so we are not overemphasise the contextual proximity.

def adjust_weights(dfg2: pd.DataFrame, weight_factor: float = 1.0) -> pd.DataFrame:
    """
    Adjust the weights in dfg2 based on the count of co-occurrences.
    weight_factor: A scaling factor to control the influence of contextual proximity.
    """
    dfg2["weight"] = dfg2["count"] * weight_factor
    return dfg2

# Merge the 2 dataframes
def merge_dataframes(dfg1: pd.DataFrame, dfg2: pd.DataFrame) -> pd.DataFrame:
    # Add a weight column to dfg1 (default weight = 1 for original relationships)
    dfg1["weight"] = 1.0
    
    # Concatenate the dataframes
    dfg = pd.concat([dfg1, dfg2], axis=0)
    
    # Group by node pairs and aggregate chunk_id, edge, and weight
    dfg = (
        dfg.groupby(["node_1", "node_2"])
        .agg({"chunk_id": ",".join, "edge": ",".join, "weight": "sum"})
        .reset_index()
    )
    
    return dfg

# Adjust weights in dfg2 (e.g., weight_factor = 0.5 to reduce the influence of contextual proximity)
dfg2 = adjust_weights(dfg2, weight_factor=0.5)

# Merge dfg1 and dfg2
dfg = merge_dataframes(dfg1, dfg2)

# Display the result
display(dfg.head())

node_1 node_2 chunk_id edge weight 0.4 m kcl fraction alpha s-casein phosphopeptides 15d3acb40240417f9954baf7773c473c,15d3acb40240417f9954baf7773c473c Contextual proximity, indicating shared meaningful relationships. 1.0 0.4 m kcl fraction alpha s-cn hydrolysate 15d3acb40240417f9954baf7773c473c,15d3acb40240417f9954baf7773c473c Contextual proximity, indicating shared meaningful relationships. 1.0 0.4 m kcl fraction beta-cn hydrolysate 15d3acb40240417f9954baf7773c473c,15d3acb40240417f9954baf7773c473c,15d3acb40240417f9954baf7773c473c Contextual proximity, indicating shared meaningful relationships. 1.5 0.4 m kcl fraction ca2+ binding 15d3acb40240417f9954baf7773c473c,15d3acb40240417f9954baf7773c473c Contextual proximity, indicating shared meaningful relationships. 1.0 0.4 m kcl fraction calcium-binding ability 15d3acb40240417f9954baf7773c473c The calcium-binding ability was found only in the fraction that was eluted with 0.4 M KCl. 1.0

##1.4. Build graphs: community detection

In [0]:
nodes = pd.concat([dfg['node_1'], dfg['node_2']], axis=0).unique()
nodes.shape

(3005,)

In [0]:
import networkx as nx
G = nx.Graph()

## Add nodes to the graph
for node in nodes:
    G.add_node(
        str(node)
    )

## Add edges to the graph
for index, row in dfg.iterrows():
    G.add_edge(
        str(row["node_1"]),
        str(row["node_2"]),
        title=row["edge"],
        weight=row['weight']
    )

In [0]:
#Calculate communities for coloring the nodes
communities_generator = nx.community.girvan_newman(G)
top_level_communities = next(communities_generator)
next_level_communities = next(communities_generator)
communities = sorted(map(sorted, next_level_communities))
print("Number of Communities = ", len(communities))
print(communities)

Number of Communities =  21
[['0.4 m kcl fraction', 'acid stress', 'acid stress response', 'acid stress survival', 'acid tolerance', 'acidic conditions', 'acidifying activities', 'acidifying activity', 'adiponectin', 'adjunct cultures', 'adjunct cultures in soft and semihard cheeses', 'aerobic ciliate models', 'alpha s-casein', 'alpha s-casein phosphopeptides', 'alpha s-cn', 'alpha s-cn hydrolysate', 'alpha s-cn solution', 'aminopeptidase a activity', 'aminopeptidase c activity', 'ammonia nitrogen concentrations', 'anion-exchange column', 'ankom in vitro gas production system', 'bacterial communities', 'bacterial protection', 'beta-cn', 'beta-cn hydrolysate', 'beta-cn phosphopeptides', 'beta-cn solution', 'body temperature', 'branched-chain fatty acids', 'bromus inermis', 'butyrate', 'butyrate concentration', 'butyrate concentrations', 'butyrate uptake', 'ca-selective electrode', 'ca2+ binding', 'cacl2 titration', 'calcium binding', 'calcium-binding ability', 'calcium-binding patterns'

In [0]:
# ### Decide to not consider the contextual proximity

# import networkx as nx

# nodes = pd.concat([dfg1['node_1'], dfg1['node_2']], axis=0).unique()

# G = nx.Graph()

# ## Add nodes to the graph
# for node in nodes:
#     G.add_node(
#         str(node)
#     )

# ## Add edges to the graph
# for index, row in dfg1.iterrows():
#     G.add_edge(
#         str(row["node_1"]),
#         str(row["node_2"]),
#         title=row["edge"],
#         weight=row['count']
#     )

# #Calculate communities for coloring the nodes
# communities_generator = nx.community.girvan_newman(G)
# top_level_communities = next(communities_generator)
# next_level_communities = next(communities_generator)
# communities = sorted(map(sorted, next_level_communities))
# print("Number of Communities = ", len(communities))
# print(communities)

Number of Communities =  399
[['0.4 m kcl fraction', 'calcium-binding ability'], ['1 wk postpartum', 'birth', 'plasma retinol', 'rrr-alpha-tocopherol'], ['1,25-dihydroxyvitamin d', 'periparturient dairy cow', 'receptor regulation'], ['1.7m diet', '2 x 3 factorial arrangement', '3.5% fcm', '4% fat-corrected milk (fcm)', '4% fcm production', '4-yr cutoff study', '5-ht concentrations', '5-ht concentrations in calves', '5-ht concentrations in colostrum', '5-ht synthesis in the mammary gland', '56-d nonreturn rate', 'aa metabolism', 'aa signaling', 'accuracy of gs model', 'acetate concentration', 'acetate-to-propionate ratio', 'acid detergent fiber', 'acid detergent insoluble protein', 'acix', 'across-production environment international genetic evaluation', 'acute pain of cautery disbudding', 'acute stressors', 'adaptation to farming environment', 'additive genetic variance', 'adhesion molecules', 'adrenocorticotropic hormone (acth)', 'age', 'albumin:globulin ratio', 'algorithms', 'allele 

In [0]:
### Decide to not consider the contextual proximity, and switch to Leiden algorithm for community detection as it has better scalability for large network

import networkx as nx
import pandas as pd
import igraph as ig
import leidenalg

nodes = pd.concat([dfg1['node_1'], dfg1['node_2']], axis=0).unique()

# Create NetworkX graph
G = nx.Graph()

# Add nodes to the graph
for node in nodes:
    G.add_node(str(node))

# Add edges to the graph
for index, row in dfg1.iterrows():
    G.add_edge(
        str(row["node_1"]),
        str(row["node_2"]),
        title=row["edge"],
        weight=row['count']
    )

# Convert NetworkX graph to igraph for Leiden algorithm
ig_graph = ig.Graph.TupleList(G.edges(data=False), directed=False)

# Apply Leiden algorithm for community detection
partition = leidenalg.find_partition(ig_graph, leidenalg.ModularityVertexPartition)

# Map Leiden communities back to NetworkX graph
for i, community in enumerate(partition):
    for node in community:
        G.nodes[str(ig_graph.vs[node]['name'])]['community'] = i

# Extract and sort communities
communities = [sorted([ig_graph.vs[node]['name'] for node in community]) for community in partition]

# Output number of communities and their members
print("Number of Communities =", len(communities))
print(communities)


Number of Communities = 762
[['350 mg of bst/14 d', '4% fat-corrected milk', 'adg', 'ala content of plasma', 'ala yield', 'alfalfa cubes', 'alh diet', 'almond hulls (alh)', 'almond hulls (alh) diet', 'arterial plasma glucose concentration', 'bias', 'biorefining of grass-clover', 'bisphenol a (bpa) supplementation', 'blood bst concentrations', 'bovine somatotropin (bst) injections', 'breeding strategies', 'brown swiss', 'bst administration', 'bst dosage', 'calving interval', 'carcass fat', 'carcass value', 'cit diet', 'cma', 'cma diet', 'cma supplement', 'cold-pressed canola', 'combined bpa and met (bpa+met) supplementation', 'con diet', 'conformation', 'conjugated linoleic acids in milk fat', 'control (con) diet', 'cow conception rate', 'cp', 'cross-countries genomic prediction', 'crossbreds', 'crushed corn', 'daily eating duration', 'daily milk protein yield', 'dairy cattle', 'dairy form', 'deregressed ebv', 'digestibility', 'digital dermatitis (dd)', 'diseases', 'dose or diet', 'dry 

In [0]:
import seaborn as sns
import random

palette = "hls"

## Now add these colors to communities and make another dataframe
def colors2Community(communities) -> pd.DataFrame:
    ## Define a color palette
    p = sns.color_palette(palette, len(communities)).as_hex()
    random.shuffle(p)
    rows = []
    group = 0
    for community in communities:
        color = p.pop()
        group += 1
        for node in community:
            rows += [{"node": node, "color": color, "group": group}]
    df_colors = pd.DataFrame(rows)
    return df_colors


colors = colors2Community(communities)
colors

node    color  group
0                     350 mg of bst/14 d  #57db6f      1
1                  4% fat-corrected milk  #57db6f      1
2                                    adg  #57db6f      1
3                  ala content of plasma  #57db6f      1
4                              ala yield  #57db6f      1
...                                  ...      ...    ...
5843                        confirmation  #cbdb57    760
5844                       aids patients  #57db58    761
5845            severe cryptosporidiosis  #57db58    761
5846  complications from other pathogens  #578cdb    762
5847          serious disease and deaths  #578cdb    762

[5848 rows x 3 columns]

In [0]:
from pyvis.network import Network

for index, row in colors.iterrows():
    G.nodes[row['node']]['group'] = row['group']
    G.nodes[row['node']]['color'] = row['color']
    G.nodes[row['node']]['size'] = G.degree[row['node']]

graph_output_directory = "/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/Results/index_test_200_no_contextual_proximity.html"

net = Network(
    notebook=False,
    # bgcolor="#1a1a1a",
    cdn_resources="remote",
    height="900px",
    width="100%",
    select_menu=True,
    # font_color="#cccccc",
    filter_menu=False,
)

net.from_nx(G)
# net.repulsion(node_distance=150, spring_length=400)
net.force_atlas_2based(central_gravity=0.015, gravity=-31)
# net.barnes_hut(gravity=-18100, central_gravity=5.05, spring_length=380)
# net.show_buttons(filter_=["physics"])

net.show(graph_output_directory, notebook=False)

/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/Results/index_test_200_no_contextual_proximity.html


In [0]:
from IPython.display import display, HTML

graph_output_directory = "/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/Results/index_test_200_no_contextual_proximity.html"
display(HTML(graph_output_directory))

## 1.5. Embed graph and filter via semantic search

In [0]:
import networkx as nx
import pandas as pd
from databricks_langchain import DatabricksEmbeddings

nodes = pd.concat([dfg1['node_1'], dfg1['node_2']], axis=0).unique()

# Create NetworkX graph
G = nx.Graph()

# Add nodes to the graph
for node in nodes:
    G.add_node(str(node))

# Add edges to the graph
for index, row in dfg1.iterrows():
    G.add_edge(
        str(row["node_1"]),
        str(row["node_2"]),
        title=row["edge"],
        weight=row['count']
    )

node_texts = {}

for node in G.nodes:
    # Get all edges for the current node
    edges = G.edges(node, data=True)
    
    # Collect edge descriptions (e.g., 'title' field or use a placeholder if missing)
    edge_descriptions = [str(data.get('title', '')) for _, _, data in edges]
    
    # Concatenate all edge descriptions to form the node text
    node_texts[node] = " ".join(edge_descriptions) if edge_descriptions else "No edge info"

print("Sample node texts:", list(node_texts.items())[:5])


Sample node texts: [('dairy industry', 'The dairy industry is increasingly using reverse osmosis (RO) membranes for concentration of various fluid feed materials. Yellow color formation is a phenomenon observed in the dairy industry, particularly in Blue Cheese production. L. delbrueckii ssp. bulgaricus is used in the dairy industry, particularly in the development and application of lactic acid bacteria. Lactic acid bacteria, including L. delbrueckii ssp. bulgaricus, have applications and uses in the dairy industry. Supercritical fluid extraction with CO(2) has great potential in the dairy industry. Lameness is a significant welfare and productivity concern in the dairy industry. The discussion of cryptosporidia, including C. muris, involves efficient concerns for the dairy industry. Cryptosporidia is a concern in the dairy industry.'), ('reverse osmosis (ro) membranes', 'The dairy industry is increasingly using reverse osmosis (RO) membranes for concentration of various fluid feed ma

In [0]:
from langchain.embeddings import DatabricksEmbeddings

# Initialize the Databricks BGE model
db_embeddings = DatabricksEmbeddings(endpoint="databricks-bge-large-en")

# Generate text embeddings using the embed_query method
node_embeddings = {node: db_embeddings.embed_query(text) for node, text in node_texts.items()}

# Check the embeddings
print("Sample node embeddings:", list(node_embeddings.items())[:5])


Sample node embeddings: [('dairy industry', [0.0157318115234375, 0.02301025390625, 0.0181884765625, 0.0188751220703125, -0.06756591796875, 0.019256591796875, -0.0018978118896484375, 0.0185089111328125, 0.0145263671875, 0.08172607421875, 0.017822265625, -0.0167694091796875, 0.03515625, -0.022674560546875, -0.03173828125, -0.00551605224609375, -0.0020294189453125, -0.051361083984375, -0.04095458984375, 0.031585693359375, 0.017242431640625, 0.024261474609375, -0.01422119140625, 0.0306854248046875, -0.055877685546875, 0.045013427734375, 0.0009889602661132812, -0.022857666015625, 0.06561279296875, 0.0301361083984375, -0.031402587890625, -0.004695892333984375, 0.03271484375, -0.078369140625, -0.00945281982421875, -0.0243072509765625, 0.03839111328125, -0.0164031982421875, -0.007049560546875, -0.04949951171875, 0.048370361328125, 0.012603759765625, 0.0699462890625, -0.059661865234375, -0.0180816650390625, 0.0019426345825195312, 0.0065460205078125, 0.0157318115234375, 0.0010929107666015625, -0

In [0]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity

# Function to find top matching nodes for a given query
def search_nodes(query, node_embeddings, top_k=50):
    query_embedding = np.array(db_embeddings.embed_query(query)).reshape(1, -1)
    
    similarities = {
        node: cosine_similarity(query_embedding, np.array(emb).reshape(1, -1))[0][0]
        for node, emb in node_embeddings.items()
    }
    
    # Sort nodes by similarity score
    return sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:top_k]

# Test: search for nodes related to an specific question
query = "what feed additives can be used to reduce methane emission"
top_nodes = search_nodes(query, node_embeddings)

print("Top matching nodes:", top_nodes)

Top matching nodes: [('methane enteric emission', 0.7761873067662536), ('dietary strategies', 0.7556996454277265), ('ch4 emissions', 0.7548410500049405), ('breeding purposes', 0.7411906523280123), ('methane (ch4) emissions', 0.7388200330994805), ('lower ch4-emissions', 0.7282982339089896), ('greenhouse gas emissions', 0.7256099014534239), ('ruminants', 0.722100275303267), ('enteric methane emissions', 0.7171802281873889), ('feeding management', 0.7115652601962819), ('beef production systems', 0.710835773868592), ('diet composition', 0.7027592293755879), ('enteric ch4 emission', 0.7010292870379811), ('dry season', 0.6987249872616893), ('ether extract', 0.6968649376288123), ('citrus pulp', 0.6956317552866401), ('enteric ch4 production', 0.6946052657190431), ('fpcm', 0.6938321073139098), ('lower ch4 emission', 0.6908641465469025), ('environmental impacts of agriculture', 0.6880654835683448), ('diet quality', 0.6875014162121296), ('breeding strategies', 0.6859045632288314), ('ch4 emissions

In [0]:
# Create a mapping from node to community, from the Leiden community clustering
node_to_community = {}
for i, community in enumerate(partition):
    for node in community:
        node_to_community[ig_graph.vs[node]['name']] = i


# Get the nodes from semantic search
matched_nodes = [node for node, score in top_nodes]

# Find the communities containing those nodes
matched_communities = {node_to_community[node] for node in matched_nodes if node in node_to_community}

# Extract all nodes in the matched communities, sorted
communities_with_nodes = [
    sorted([node for node, comm in node_to_community.items() if comm == community_id])
    for community_id in matched_communities
]

print("Total communities:", len(communities_with_nodes))

Total communities: 18


In [0]:
import seaborn as sns
import random
from pyvis.network import Network
from IPython.display import display, HTML

palette = "hls"

## Now add these colors to communities and make another dataframe
def colors2Community(communities) -> pd.DataFrame:
    ## Define a color palette
    p = sns.color_palette(palette, len(communities)).as_hex()
    random.shuffle(p)
    rows = []
    group = 0
    for community in communities:
        color = p.pop()
        group += 1
        for node in community:
            rows += [{"node": node, "color": color, "group": group}]
    df_colors = pd.DataFrame(rows)
    return df_colors


colors = colors2Community(communities_with_nodes)


for index, row in colors.iterrows():
    G.nodes[row['node']]['group'] = row['group']
    G.nodes[row['node']]['color'] = row['color']
    G.nodes[row['node']]['size'] = G.degree[row['node']]

graph_output_directory = "/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/Results/index_test_200_filtered_topic.html"

net = Network(
    notebook=False,
    cdn_resources="remote",
    height="900px",
    width="100%",
    select_menu=True,
    filter_menu=False,
)

net.from_nx(G)
net.force_atlas_2based(central_gravity=0.015, gravity=-31)
net.show(graph_output_directory, notebook=False)

display(HTML(graph_output_directory))

/Workspace/Users/el839@cornell.edu/3_OntologyLLM/Data/Results/index_test_200_filtered_topic.html
